## Exercise : Extracting data from OFET-DB to perform ML

Its great that we have data stored in a standardized manner in our database but now we need to extract data from this database in the form of a table containing descriptors [X] and property [y] to perform ML. This notebook will focus on how we can do that. 

First i want you to use the backup file called 20231206_ofetdb_v2_backup11 and add it to your pgadmin as a practice database. We will avoid working with the original database.

In [1]:
# Connect to the database


import psycopg2
import pandas as pd
import numpy as np
import plotly.express as px


#sample connection details
# pgparams = {
#     "host": "127.0.0.1",
#     "database": "ofetdb_testenv",
#     "user": "postgres",
#     "password": "password",
#     "port": "5432",
# }


# Set max number of displayed columns and rows in Jupyter Notebook
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


pgparams = {
    "host": "chbe-ofet-db.postgres.database.azure.com",
    "database": "ofetdb_v2_test",
    "user": "mg200_ofetdb",
    "password": "MGEROFETDB23!",
    "port": "5432",
}

def read_select_query(query):

    with psycopg2.connect(**pgparams) as conn:

        df = pd.read_sql_query(query, conn)

    return df


## Simplest Scenario :

- assume only single polymer scenarios, no blends first (wt_frac = 1)
- assume only single solvent scenarios, no multiple solvents (vol_frac = 1)
- show device substrate information 
- show film deposition information (spin, blade, etc). We will not use the parameters for now
- dont go into detail of solution treatment, substrate pretreat and post process. Just show if treatment was performed
- show hole mobility information

Follow the code blocks below and we will eventually end up with a table containing this information 

1. Prepare a dataframe containing the sample_Id, citation_type and meta information from the experimental table (This one is done as a practice for you)

In [20]:
## Adding all the experiment information 

# SQL query to fetch the required data
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id;
'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

# Display the resulting DataFrame
#print(result_df)

result_df

C:\Users\jbonsu3\AppData\Local\Temp\ipykernel_20988\1089282080.py:37: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query, conn)


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          13    literature   
13          14    literature   
14          15    literature   
15          16    literature   
16          17    literature   
17          18    literature   
18          19    literature   
19          20    literature   
20          21    literature   
21          22    literature   
22          23    literature   
23          24    literature   
24          25    literature   
25          26    literature   
26          27    literature   
27          28    literature   
28          29    literature   
29          30    literature   
30          31    literature   
31          32    literature   
32          33    literature   
33          34    literature   
34          35    literature   
35          36    literature   
36          37    literature   
37          38    literature   
38          39    literature   
39          40    literature   
40          41    literature   
41          42    literature   
42          43    literature   
43          44    literature   
44          45    literature   
45          46    literature   
46          47    literature   
47          48    literature   
48          49    literature   
49          50    literature   
50          51    literature   
51          52    literature   
52          53    literature   
53          54    literature   
54          55    literature   
55          56    literature   
56          57    literature   
57          58    literature   
58          59    literature   
59          60    literature   
60          61    literature   
61          62    literature   
62          63    literature   
63          64    literature   
64          65    literature   
65          66    literature   
66          67    literature   
67          68    literature   
68          69    literature   
69          70    literature   
70          71    literature   
71          72    literature   
72          73    literature   
73          74    literature   
74          75    literature   
75          76    literature   
76          77    literature   
77          78    literature   
78          79    literature   
79          80    literature   
80          81    literature   
81          82    literature   
82          83    literature   
83          84    literature   
84          85    literature   
85          86    literature   
86          87    literature   
87          88    literature   
88          89    literature   
89          90    literature   
90          91    literature   
91          92    literature   
92          93    literature   
93          94    literature   
94          95    literature   
95          96    literature   
96          97    literature   
97          98    literature   
98          99    literature   
99         100    literature   
100        101    literature   
101        102    literature   
102        103    literature   
103        104    literature   
104        105    literature   
105        106    literature   
106        107    literature   
107        108    literature   
108        109    literature   
109        110    literature   
110        111    literature   
111        112    literature   
112        113    literature   
113        114    literature   
114        115    literature   
115        116    literature   
116        117    literature   
117        118    literature   
118        119    literature   
119        120    literature   
120        121    literature   
121        122    literature   
122        123    literature   
123        124    literature   
124  

remember to keep adding to the existing query to add more information to the table. It is going to get complicated and long soon FYI. 

2. Now to this database add the solution concentration information

In [13]:
## only way to join is through ofet_process

query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON s.process_id = sms.solution_id
    LEFT JOIN
        SOLUTION sol ON sms.solution_id = sol.solution_id ;
'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

result_df

C:\Users\jbonsu3\AppData\Local\Temp\ipykernel_6316\1089282080.py:37: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query, conn)


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          13    literature   
13          14    literature   
14          15    literature   
15          16    literature   
16          17    literature   
17          18    literature   
18          19    literature   
19          20    literature   
20          21    literature   
21          22    literature   
22          23    literature   
23          24    literature   
24          25    literature   
25          26    literature   
26          27    literature   
27          28    literature   
28          29    literature   
29          30    literature   
30          31    literature   
31          32    literature   
32          33    literature   
33          34    literature   
34          35    literature   
35          36    literature   
36          37    literature   
37          38    literature   
38          38    literature   
39          39    literature   
40          40    literature   
41          40    literature   
42          41    literature   
43          41    literature   
44          42    literature   
45          42    literature   
46          43    literature   
47          44    literature   
48          45    literature   
49          46    literature   
50          47    literature   
51          48    literature   
52          49    literature   
53          50    literature   
54          51    literature   
55          52    literature   
56          53    literature   
57          54    literature   
58          55    literature   
59          56    literature   
60          57    literature   
61          58    literature   
62          59    literature   
63          60    literature   
64          61    literature   
65          62    literature   
66          63    literature   
67          64    literature   
68          65    literature   
69          66    literature   
70          67    literature   
71          68    literature   
72          69    literature   
73          70    literature   
74          71    literature   
75          72    literature   
76          73    literature   
77          74    literature   
78          75    literature   
79          76    literature   
80          77    literature   
81          78    literature   
82          79    literature   
83          80    literature   
84          81    literature   
85          82    literature   
86          83    literature   
87          84    literature   
88          85    literature   
89          86    literature   
90          87    literature   
91          88    literature   
92          89    literature   
93          90    literature   
94          91    literature   
95          92    literature   
96          93    literature   
97          94    literature   
98          95    literature   
99          96    literature   
100         97    literature   
101         98    literature   
102         99    literature   
103        100    literature   
104        101    literature   
105        102    literature   
106        103    literature   
107        104    literature   
108        105    literature   
109        106    literature   
110        107    literature   
111        108    literature   
112        109    literature   
113        110    literature   
114        111    literature   
115        112    literature   
116        113    literature   
117        114    literature   
118        115    literature   
119        115    literature   
120        116    literature   
121        117    literature   
122        118    literature   
123        119    literature   
124  

3. Now to this table add the solvent information but only consider devices made from single solvent vol frac = 1

In [ ]:
## only way to join is through ofet_process

query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sms.vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON s.process_id = sms.solution_id
    LEFT JOIN
        SOLUTION sol ON sms.solution_id = sol.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    WHERE 
        sms.vol_frac = 1;
'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

result_df

4. Now to this table add polymer information only for devices made from one polymer (no blends) (wt-frac = 1)

In [ ]:
## only way to join is through ofet_process

query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sms.vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        smp.wt_frac
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON s.process_id = sms.solution_id
    LEFT JOIN
        SOLUTION sol ON sms.solution_id = sol.solution_id
    LEFT JOIN 
        SOLUTION_MAKEUP_POLYMER smp ON s.process_id = smp.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    WHERE 
        sms.vol_frac=1 and smp.wt_frac=1;
'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

result_df

5. Now to this table add the device substrate information 

In [ ]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sol.concentration,
        sms.vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        smp.wt_frac,
        dev.params
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON s.process_id = sms.solution_id
    LEFT JOIN
        SOLUTION sol ON sms.solution_id = sol.solution_id
    LEFT JOIN 
        SOLUTION_MAKEUP_POLYMER smp ON s.process_id = smp.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        OFET_PROCESS of ON s.process_id =of.process_id
    LEFT JOIN
        DEVICE_FABRICATION dev ON dev.device_fab_id = of.device_fab_id
    WHERE 
        sms.vol_frac=1 and smp.wt_frac=1;

'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

result_df

6. Now to this table add the film deposition type only not the parameters associated with it

In [ ]:
query = '''
  SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sol.concentration,
        sms.vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        smp.wt_frac,
        dev.params,
        fd.deposition_type
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON s.process_id = sms.solution_id
    LEFT JOIN
        SOLUTION sol ON sms.solution_id = sol.solution_id
    LEFT JOIN 
        SOLUTION_MAKEUP_POLYMER smp ON s.process_id = smp.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        OFET_PROCESS of ON s.process_id =of.process_id
    LEFT JOIN
        DEVICE_FABRICATION dev ON dev.device_fab_id = of.device_fab_id
    LEFT JOIN
        FILM_DEPOSITION fd ON of.process_id = fd.film_deposition_id
    WHERE 
        sms.vol_frac=1 and smp.wt_frac=1;

'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

result_df

7. Now to this table add the solution treatment, substrate preatreat and post process informaiton 

1 if treatment is done and 0 if no treatment



In [ ]:
query = '''
      SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sol.concentration,
        sms.vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        smp.wt_frac,
        dev.params,
        fd.deposition_type,
    CASE
        WHEN ststep.treatment_type is not NULL then '1'
        ELSE '0'
    END AS SOLUTION_TREATMENT,
    CASE
        WHEN spstep.treatment_type is not NULL then '1'
        ELSE '0'
    END AS SUBSTRATE_PRETREAT,
    CASE
        WHEN ppstep.treatment_type is not NULL then '1'
        ELSE '0'
    END AS POST_PROCESS
    
FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON s.process_id = sms.solution_id
    LEFT JOIN
        SOLUTION sol ON sms.solution_id = sol.solution_id
    LEFT JOIN 
        SOLUTION_MAKEUP_POLYMER smp ON s.process_id = smp.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        OFET_PROCESS of ON s.process_id =of.process_id
    LEFT JOIN
        DEVICE_FABRICATION dev ON dev.device_fab_id = of.device_fab_id
    LEFT JOIN
        FILM_DEPOSITION fd ON of.process_id = fd.film_deposition_id
    LEFT JOIN
        SOLUTION_TREATMENT st ON st.solution_treatment_id = of.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_ORDER sto ON sto.solution_treatment_id =st.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_STEP ststep ON ststep.solution_treatment_step_id = sto.solution_treatment_step_id
    LEFT JOIN
       SUBSTRATE_PRETREAT sp ON sp.substrate_pretreat_id = of.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_ORDER spo ON spo.substrate_pretreat_id = sp.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_STEP spstep ON spstep.substrate_pretreat_step_id = spo.substrate_pretreat_step_id
    LEFT JOIN
        POSTPROCESS pp ON pp.postprocess_id = of.postprocess_id 
    LEFT JOIN
        POSTPROCESS_ORDER ppo ON ppo.postprocess_id = pp.postprocess_id
    LEFT JOIN
        POSTPROCESS_STEP ppstep ON ppstep.postprocess_step_id = ppo.postprocess_step_id
    WHERE 
        sms.vol_frac=1 and smp.wt_frac=1;
'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

result_df

8. Now to this table add the hole mobility information 

only keep devices that have an actual hole mobility value and is not Null or NAN

In [2]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration as solution_concentration,
        sms.vol_frac as solvent_vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        p.common_name as polymer_common_name,
        p.iupac_name as polymer_iupac_name,
        p.mw as polymer_mw,
        p.mn as polymer_mn,
        p.dispersity as polymer_dispersity,
        dev.params as device_substrate_parameters,
        fd.deposition_type as film_deposition_type,
        fd.params as film_deposition_params,
        
    CASE
        WHEN ststep.treatment_type is not NULL then '1'
        ELSE '0'
    END AS SOLUTION_TREATMENT,
    CASE
        WHEN spstep.treatment_type is not NULL then '1'
        ELSE '0'
    END AS SUBSTRATE_PRETREAT,
    CASE
        WHEN ppstep.treatment_type is not NULL then '1'
        ELSE '0'
    END AS POST_PROCESS,
    CAST(meas.data-> 'hole_mobility'->>'value' AS float) AS hole_mobility
    
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON s.process_id = sms.solution_id
    LEFT JOIN
        SOLUTION sol ON sms.solution_id = sol.solution_id
    LEFT JOIN 
        SOLUTION_MAKEUP_POLYMER smp ON s.process_id = smp.solution_id
    LEFT JOIN
        POLYMER p ON smp.polymer_id = p.polymer_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        OFET_PROCESS of ON s.process_id =of.process_id
    LEFT JOIN
        DEVICE_FABRICATION dev ON dev.device_fab_id = of.device_fab_id
    LEFT JOIN
        FILM_DEPOSITION fd ON of.process_id = fd.film_deposition_id
    LEFT JOIN
        SOLUTION_TREATMENT st ON st.solution_treatment_id = of.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_ORDER sto ON sto.solution_treatment_id =st.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_STEP ststep ON ststep.solution_treatment_step_id = sto.solution_treatment_step_id
    LEFT JOIN
       SUBSTRATE_PRETREAT sp ON sp.substrate_pretreat_id = of.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_ORDER spo ON spo.substrate_pretreat_id = sp.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_STEP spstep ON spstep.substrate_pretreat_step_id = spo.substrate_pretreat_step_id
    LEFT JOIN
        POSTPROCESS pp ON pp.postprocess_id = of.postprocess_id 
    LEFT JOIN
        POSTPROCESS_ORDER ppo ON ppo.postprocess_id = pp.postprocess_id
    LEFT JOIN
        POSTPROCESS_STEP ppstep ON ppstep.postprocess_step_id = ppo.postprocess_step_id
    LEFT JOIN
        MEASUREMENT meas ON s.sample_id = meas.sample_id
        
    WHERE 
        sms.vol_frac=1 
        AND smp.wt_frac=1
        AND (meas.data->> 'hole_mobility' IS NOT NULL OR meas.data->> 'hole_mobility' = 'NAN');
'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3           12    literature   
4           13    literature   
5           14    literature   
6           15    literature   
7           23    literature   
8           24    literature   
9           25    literature   
10          26    literature   
11          27    literature   
12          28    literature   
13          29    literature   
14          30    literature   
15          31    literature   
16          32    literature   
17          33    literature   
18          34    literature   
19          35    literature   
20          36    literature   
21          39    literature   
22          45    literature   
23          46    literature   
24          49    literature   
25          50    literature   
26          51    literature   
27          52    literature   
28          53    literature   
29          54    literature   
30          55    literature   
31          56    literature   
32          57    literature   
33          58    literature   
34          59    literature   
35          60    literature   
36          61    literature   
37          62    literature   
38          63    literature   
39          64    literature   
40          65    literature   
41          66    literature   
42          67    literature   
43          68    literature   
44          69    literature   
45          70    literature   
46          71    literature   
47          72    literature   
48          73    literature   
49          74    literature   
50          75    literature   
51          76    literature   
52          77    literature   
53          78    literature   
54          87    literature   
55          88    literature   
56          89    literature   
57          90    literature   
58          91    literature   
59          92    literature   
60          93    literature   
61          94    literature   
62          95    literature   
63          96    literature   
64          97    literature   
65          98    literature   
66          99    literature   
67         100    literature   
68         101    literature   
69         102    literature   
70         103    literature   
71         104    literature   
72         105    literature   
73         106    literature   
74         107    literature   
75         108    literature   
76         109    literature   
77         110    literature   
78         111    literature   
79         112    literature   
80         113    literature   
81         114    literature   
82         116    literature   
83         117    literature   
84         118    literature   
85         119    literature   
86         120    literature   
87         121    literature   
88         122    literature   
89         123    literature   
90         124    literature   
91         125    literature   
92         126    literature   
93         127    literature   
94         128    literature   
95         136    laboratory   
96         137    laboratory   
97         190    literature   
98         152    laboratory   
99         153    laboratory   
100        155    laboratory   
101        156    laboratory   
102        157    laboratory   
103        158    laboratory   
104        159    laboratory   
105        160    laboratory   
106        161    laboratory   
107        163    laboratory   
108        168    laboratory   
109        169    laboratory   
110        170    laboratory   
111        171    laboratory   
112        172    laboratory   
113        173    laboratory   
114        174    laboratory   
115        175    laboratory   
116        176    laboratory   
117        177    laboratory   
118        178    laboratory   
119        179    literature   
120        180    literature   
121        181    literature   
122        183    literature   
123        184    literature   
124  

This is a simple version of the dataframe result_df. There are a couple more things we can now do to the dataframe to make it more machine readable. We no longer need to use sql queries. can just work with the dataframe and pandas

9. The code block below will unpack the data stored in device_substrate_parameters and store it as columns (this one is done for you)

In [3]:
 #unpacking the information stored in device_substrate_parameters

import pandas as pd
from pandas import json_normalize


# # Extract the 'device_substrate_parameters' column and normalize it
params_df = json_normalize(result_df['device_substrate_parameters'])

# # Concatenate the original DataFrame with the new 'params_df'
result_df = pd.concat([result_df, params_df], axis=1)

# # Drop the original 'device_substrate_parameters' column
result_df_norm = result_df.drop('device_substrate_parameters', axis=1)

# # Display the resulting DataFrame
result_df_norm

sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3           12    literature   
4           13    literature   
5           14    literature   
6           15    literature   
7           23    literature   
8           24    literature   
9           25    literature   
10          26    literature   
11          27    literature   
12          28    literature   
13          29    literature   
14          30    literature   
15          31    literature   
16          32    literature   
17          33    literature   
18          34    literature   
19          35    literature   
20          36    literature   
21          39    literature   
22          45    literature   
23          46    literature   
24          49    literature   
25          50    literature   
26          51    literature   
27          52    literature   
28          53    literature   
29          54    literature   
30          55    literature   
31          56    literature   
32          57    literature   
33          58    literature   
34          59    literature   
35          60    literature   
36          61    literature   
37          62    literature   
38          63    literature   
39          64    literature   
40          65    literature   
41          66    literature   
42          67    literature   
43          68    literature   
44          69    literature   
45          70    literature   
46          71    literature   
47          72    literature   
48          73    literature   
49          74    literature   
50          75    literature   
51          76    literature   
52          77    literature   
53          78    literature   
54          87    literature   
55          88    literature   
56          89    literature   
57          90    literature   
58          91    literature   
59          92    literature   
60          93    literature   
61          94    literature   
62          95    literature   
63          96    literature   
64          97    literature   
65          98    literature   
66          99    literature   
67         100    literature   
68         101    literature   
69         102    literature   
70         103    literature   
71         104    literature   
72         105    literature   
73         106    literature   
74         107    literature   
75         108    literature   
76         109    literature   
77         110    literature   
78         111    literature   
79         112    literature   
80         113    literature   
81         114    literature   
82         116    literature   
83         117    literature   
84         118    literature   
85         119    literature   
86         120    literature   
87         121    literature   
88         122    literature   
89         123    literature   
90         124    literature   
91         125    literature   
92         126    literature   
93         127    literature   
94         128    literature   
95         136    laboratory   
96         137    laboratory   
97         190    literature   
98         152    laboratory   
99         153    laboratory   
100        155    laboratory   
101        156    laboratory   
102        157    laboratory   
103        158    laboratory   
104        159    laboratory   
105        160    laboratory   
106        161    laboratory   
107        163    laboratory   
108        168    laboratory   
109        169    laboratory   
110        170    laboratory   
111        171    laboratory   
112        172    laboratory   
113        173    laboratory   
114        174    laboratory   
115        175    laboratory   
116        176    laboratory   
117        177    laboratory   
118        178    laboratory   
119        179    literature   
120        180    literature   
121        181    literature   
122        183    literature   
123        184    literature   
124  

In [4]:

# Drop unnecessary columns that won't be used for modeling
columns_to_drop = ['film_deposition_params', 'citation_type', 'experiment_meta', 'solvent_vol_frac', 'solvent_iupac_name', 'polymer_iupac_name']
result_df = result_df_norm.drop(columns=columns_to_drop)

# Display the resulting DataFrame
result_df


sample_id  solution_concentration  solvent_pubchem_cid  \
0            1                   4.000                 7964   
1            2                   4.000                 7964   
2            3                   5.000                 6212   
3           12                   5.000                 7964   
4           13                   5.000                 7964   
5           14                   5.000                 7964   
6           15                   4.000                 7239   
7           23                   6.500                 6212   
8           24                   3.000                 7239   
9           25                   7.000                 7239   
10          26                   6.500                 6212   
11          27                   1.600                 6212   
12          28                   0.500                 6212   
13          29                   0.500                 6212   
14          30                   0.500                 6212   
15          31                   0.500                 6212   
16          32                   0.750                 6212   
17          33                   1.000                 6212   
18          34                   2.000                 6212   
19          35                   5.000                 6212   
20          36                   2.000                 7239   
21          39                   4.000                 6212   
22          45                   5.000                 6212   
23          46                   5.000                 6212   
24          49                   5.000                 6212   
25          50                   5.000                 6212   
26          51                   7.000                 6212   
27          52                   8.500                 6212   
28          53                  10.000                 6212   
29          54                  12.000                 6212   
30          55                  14.000                 6212   
31          56                  16.000                 6212   
32          57                  18.000                 6212   
33          58                  25.000                 6212   
34          59                   3.000                 6212   
35          60                   3.000                 7964   
36          61                   4.000                 7964   
37          62                   5.000                 7964   
38          63                   6.000                 7964   
39          64                   8.000                 7964   
40          65                   5.000                 7239   
41          66                  10.000                 7239   
42          67                   8.000                 6212   
43          68                  12.000                 6212   
44          69                  27.000                 6212   
45          70                   4.000                 7239   
46          71                   2.000                 7964   
47          72                   4.000                 7239   
48          73                   2.000                 7964   
49          74                   6.000                 7964   
50          75                  10.000                 7964   
51          76                   5.000                 7964   
52          77                   5.000                 7964   
53          78                   5.000                 7964   
54          87                   4.000                 7964   
55          88                   7.000                 7964   
56          89                   8.000                 7964   
57          90                   2.000                 7964   
58          91                   4.000                 7964   
59          92                   6.000                 7964   
60          93                   8.000                 7964   
61          94                   9.000                 7964   
62          95                  10.0

We are now going to do something called one hot encoding to convert columns with textual information into numbers (1 and 0)

In [ ]:
# List of columns to one-hot encode
#columns_to_one_hot_encode = ['film_deposition_type', 'gate_material', 'dielectric_material', 'electrode_configuration']
columns_to_one_hot_encode = ['film_deposition_type', 'gate_material', 'electrode_configuration']

# Perform one-hot encoding
result_df_hot = pd.get_dummies(result_df_norm, columns=columns_to_one_hot_encode)

# Display the resulting DataFrame with one-hot encoding
result_df_hot


Now lets see all the columns in this database 

In [ ]:
column_names = result_df_hot.columns
print(column_names)


### Consolidating Descriptors

We are going to consolidate some of the descriptors into one column. 


Coating :

* film_deposition_type_MGC (dip,Dip,blade, inkjet, shear, wire) - value of 1 if any of these columns are true or else 0
* film_deposition_type_spin
* film_deposition_type_drop

Gate Material :

* gate_material_n_doped Si = ('gate_material_n-doped Si', 'gate_material_Si','gate_material_p-doped Si') 

* gate_material_other = ('gate_material_Al', 'gate_material_Au', 'gate_material_PEDOT:PSS', 'gate_material_PET','gate_material_glass')


Dielectric Material :

* dielectric_material_SiO2
* dielectric_material_other = (
        'dielectric_material_6FDA-DABC',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_material_Shellac',
       'dielectric_material_Si3N4')




In [ ]:
result_df_hot

In [ ]:
## replacing the pubchem_cid with solvent boiling point

# Get unique PubChem CIDs from the 'solvent_pubchem_cid' column
unique_pubchem_cids = result_df['solvent_pubchem_cid'].unique()

# Display the unique PubChem CIDs
print(unique_pubchem_cids)



In [ ]:
# Dictionary mapping PubChem CIDs to boiling points
boiling_point_dict = {
    7964: 132,
    6212: 62,
    7239: 180.1,
    6591: 146,
    7809: 138,
    13229: 238,
    13: 213,
    8030: 84,
    1140: 111,
    7501: 145,
    241: 80,
    6344: 40,
    7503: 179
}

# Add a new column "solvent_boiling_point" based on PubChem CIDs
result_df['solvent_boiling_point'] = result_df['solvent_pubchem_cid'].map(boiling_point_dict)


# Drop unnecessary columns that won't be used for modeling
columns_to_drop = ['solvent_pubchem_cid']
result_df = result_df.drop(columns=columns_to_drop)

# Display the resulting DataFrame
result_df


In [ ]:
column_names = result_df.columns
print(column_names)

In [ ]:
result_df_P3HT = result_df[result_df['polymer_common_name'] == 'P3HT']
result_df_DPP_DTT = result_df[result_df['polymer_common_name'] != 'P3HT']


### P3HT Modeling

In [ ]:
result_df_P3HT = result_df_P3HT.drop(columns='polymer_common_name')
result_df_P3HT

In [ ]:
num_rows, num_columns = result_df_P3HT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")


### DPP-DTT Modeling

In [ ]:
result_df_DPP_DTT = result_df_DPP_DTT.drop(columns='polymer_common_name')
result_df_DPP_DTT

In [ ]:
num_rows, num_columns = result_df_DPP_DTT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")


In [ ]:
###EXTRACTION PART2
# make each solution processing, substarte pretreat and post processing type into individual column
# have the step number in each type. if done mixing first then 1 second step should have 2

In [ ]:
# 1. determine what process/treatment is possible in each(start with 1 then expand)
# 2. make a table for each procee/treatment
# 3. input a 1 or 2 or etc for the step each treatment was done, 0 if not done

In [7]:
query = '''
    SELECT
        s.sample_id,
        spo.process_order AS substrate_pretreat_order,
        spstep.treatment_type AS substrate_pretreat_type,
        sto.process_order AS solution_treatment_order,
        ststep.treatment_type AS solution_treatment_type,
        ppo.process_order AS post_process_order,
        ppstep.treatment_type AS post_process_type
    FROM
        SAMPLE s
    JOIN
        OFET_PROCESS of ON s.process_id = of.process_id
    LEFT JOIN 
        SUBSTRATE_PRETREAT_ORDER spo ON of.substrate_pretreat_id = spo.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_STEP spstep ON spstep.substrate_pretreat_step_id = spo.substrate_pretreat_step_id
    LEFT JOIN
        SOLUTION_TREATMENT_ORDER sto ON of.solution_treatment_id = sto.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_STEP ststep ON sto.solution_treatment_step_id = ststep.solution_treatment_step_id
    LEFT JOIN
        POSTPROCESS_ORDER ppo ON of.postprocess_id = ppo.postprocess_id
    LEFT JOIN
        POSTPROCESS_STEP ppstep ON ppo.postprocess_step_id = ppstep.postprocess_step_id
    '''

#join order and step through step id

result_df_order = read_select_query(query)

result_df_order

C:\Users\jbonsu3\AppData\Local\Temp\ipykernel_20988\1089282080.py:37: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query, conn)


sample_id  substrate_pretreat_order substrate_pretreat_type  \
0             1                       NaN                    None   
1             2                       1.0                     sam   
2             3                       1.0                     sam   
3             4                       1.0                     sam   
4             5                       1.0                     sam   
5             6                       2.0                     sam   
6             6                       1.0                     sam   
7             7                       2.0                     sam   
8             7                       1.0                     sam   
9             8                       2.0                     sam   
10            8                       1.0                     sam   
11            9                       2.0                     sam   
12            9                       1.0                     sam   
13           10                       2.0                     sam   
14           10                       1.0                     sam   
15           11                       2.0                     sam   
16           11                       1.0                     sam   
17           12                       NaN                    None   
18           13                       NaN                    None   
19           14                       NaN                    None   
20           15                       NaN                    None   
21           16                       NaN                    None   
22           17                       NaN                    None   
23           18                       NaN                    None   
24           19                       NaN                    None   
25           20                       NaN                    None   
26           21                       NaN                    None   
27           22                       NaN                    None   
28           23                       NaN                    None   
29           24                       1.0                     sam   
30           25                       1.0                     sam   
31           26                       1.0                     sam   
32           27                       1.0                     sam   
33           28                       1.0                     sam   
34           29                       1.0                     sam   
35           30                       1.0                     sam   
36           31                       1.0                     sam   
37           32                       1.0                     sam   
38           33                       1.0                     sam   
39           34                       1.0                     sam   
40           35                       1.0                     sam   
41           36                       1.0                     sam   
42           37                       1.0                     sam   
43           38                       1.0                     sam   
44           39                       1.0                     sam   
45           40                       1.0                     sam   
46           41                       1.0                     sam   
47           42                       1.0                     sam   
48           43                       NaN                    None   
49           44                       NaN                    None   
50           45                       NaN                    None   
51           46                       NaN                    None   
52           47                       NaN                    None   
53           48                       NaN                    None   
54           49                       NaN                    None   
55           50                       NaN                    None   
56           51                       1.0                     sam   
57  

In [2]:
##consider processing with order
query = '''
   SELECT
    s.sample_id,
    COALESCE(MAX(CASE WHEN spstep.treatment_type = 'sam' THEN spo.process_order END), 0) AS substrate_pretreat_sam,
    COALESCE(MAX(CASE WHEN spstep.treatment_type = 'plasma' THEN spo.process_order END), 0) AS substrate_pretreat_plasma,
    COALESCE(MAX(CASE WHEN spstep.treatment_type = 'uv_ozone' THEN spo.process_order END), 0) AS substrate_pretreat_uv_ozone,
    
    COALESCE(MAX(CASE WHEN ststep.treatment_type = 'poor_solvent' THEN sto.process_order END), 0) AS solution_treatment_poor_solvent,
    COALESCE(MAX(CASE WHEN ststep.treatment_type = 'aging' THEN sto.process_order END), 0) AS solution_treatment_aging,
    COALESCE(MAX(CASE WHEN ststep.treatment_type = 'sonication' THEN sto.process_order END), 0) AS solution_treatment_sonication,
    COALESCE(MAX(CASE WHEN ststep.treatment_type = 'mixing' THEN sto.process_order END), 0) AS solution_treatment_mixing,
    COALESCE(MAX(CASE WHEN ststep.treatment_type = 'uv_irradiation' THEN sto.process_order END), 0) AS solution_treatment_uv_irradiation,
    
    COALESCE(MAX(CASE WHEN ppstep.treatment_type = 'annealing' THEN ppo.process_order END), 0) AS post_process_annealing,
    COALESCE(MAX(CASE WHEN ppstep.treatment_type = 'drying' THEN ppo.process_order END), 0) AS post_process_drying,
    COALESCE(MAX(CASE WHEN ppstep.treatment_type = 'chemical_treat' THEN ppo.process_order END), 0) AS post_process_chemical



     FROM
        SAMPLE s
    JOIN
        OFET_PROCESS of ON s.process_id = of.process_id
    LEFT JOIN 
        SUBSTRATE_PRETREAT_ORDER spo ON of.substrate_pretreat_id = spo.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_STEP spstep ON spstep.substrate_pretreat_step_id = spo.substrate_pretreat_step_id
    LEFT JOIN
        SOLUTION_TREATMENT_ORDER sto ON of.solution_treatment_id = sto.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_STEP ststep ON sto.solution_treatment_step_id = ststep.solution_treatment_step_id
    LEFT JOIN
        POSTPROCESS_ORDER ppo ON of.postprocess_id = ppo.postprocess_id
    LEFT JOIN
        POSTPROCESS_STEP ppstep ON ppo.postprocess_step_id = ppstep.postprocess_step_id
    GROUP BY
        s.sample_id
    ORDER BY
        s.sample_id ASC;


'''

# Use the read_select_query function to execute the query
result_df_order = read_select_query(query)

result_df_order    

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id  substrate_pretreat_sam  substrate_pretreat_plasma  \
0            1                       0                          0   
1            2                       1                          0   
2            3                       1                          0   
3            4                       1                          0   
4            5                       1                          0   
5            6                       2                          0   
6            7                       2                          0   
7            8                       2                          0   
8            9                       2                          0   
9           10                       2                          0   
10          11                       2                          0   
11          12                       0                          0   
12          13                       0                          0   
13          14                       0                          0   
14          15                       0                          0   
15          16                       0                          0   
16          17                       0                          0   
17          18                       0                          0   
18          19                       0                          0   
19          20                       0                          0   
20          21                       0                          0   
21          22                       0                          0   
22          23                       0                          0   
23          24                       1                          0   
24          25                       1                          0   
25          26                       1                          0   
26          27                       1                          0   
27          28                       1                          0   
28          29                       1                          0   
29          30                       1                          0   
30          31                       1                          0   
31          32                       1                          0   
32          33                       1                          0   
33          34                       1                          0   
34          35                       1                          0   
35          36                       1                          0   
36          37                       1                          0   
37          38                       1                          0   
38          39                       1                          0   
39          40                       1                          0   
40          41                       1                          0   
41          42                       1                          0   
42          43                       0                          0   
43          44                       0                          0   
44          45                       0                          0   
45          46                       0                          0   
46          47                       0                          0   
47          48                       0                          0   
48          49                       0                          0   
49          50                       0                          0   
50          51                       1                          0   
51          52                       1                          0   
52          53                       1                          0   
53          54                       1                          0   
54          55                       0                          0   
55          56                       1                          0   
56          57                       1                          0   
57 

In [ ]:
#one hot encoding for all processing, no order considered
#download python tpot, first cell for pipeline gnerator file

In [21]:
query = '''
    SELECT
        s.sample_id,
        spo.process_order AS substrate_pretreat_order,
        spstep.treatment_type AS substrate_pretreat_type,
        spstep.params AS substrate_pretreat_params,
        sto.process_order AS solution_treatment_order,
        ststep.treatment_type AS solution_treatment_type,
        ppo.process_order AS post_process_order,
        ppstep.treatment_type AS post_process_type
    FROM
        SAMPLE s
    JOIN
        OFET_PROCESS of ON s.process_id = of.process_id
    LEFT JOIN 
        SUBSTRATE_PRETREAT_ORDER spo ON of.substrate_pretreat_id = spo.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_STEP spstep ON spstep.substrate_pretreat_step_id = spo.substrate_pretreat_step_id
    LEFT JOIN
        SOLUTION_TREATMENT_ORDER sto ON of.solution_treatment_id = sto.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_STEP ststep ON sto.solution_treatment_step_id = ststep.solution_treatment_step_id
    LEFT JOIN
        POSTPROCESS_ORDER ppo ON of.postprocess_id = ppo.postprocess_id
    LEFT JOIN
        POSTPROCESS_STEP ppstep ON ppo.postprocess_step_id = ppstep.postprocess_step_id
    '''

#join order and step through step id

result_df_chem = read_select_query(query)

result_df_chem

C:\Users\jbonsu3\AppData\Local\Temp\ipykernel_20988\1089282080.py:37: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query, conn)


sample_id  substrate_pretreat_order substrate_pretreat_type  \
0             1                       NaN                    None   
1             2                       1.0                     sam   
2             3                       1.0                     sam   
3             4                       1.0                     sam   
4             5                       1.0                     sam   
5             6                       2.0                     sam   
6             6                       1.0                     sam   
7             7                       2.0                     sam   
8             7                       1.0                     sam   
9             8                       2.0                     sam   
10            8                       1.0                     sam   
11            9                       2.0                     sam   
12            9                       1.0                     sam   
13           10                       2.0                     sam   
14           10                       1.0                     sam   
15           11                       2.0                     sam   
16           11                       1.0                     sam   
17           12                       NaN                    None   
18           13                       NaN                    None   
19           14                       NaN                    None   
20           15                       NaN                    None   
21           16                       NaN                    None   
22           17                       NaN                    None   
23           18                       NaN                    None   
24           19                       NaN                    None   
25           20                       NaN                    None   
26           21                       NaN                    None   
27           22                       NaN                    None   
28           23                       NaN                    None   
29           24                       1.0                     sam   
30           25                       1.0                     sam   
31           26                       1.0                     sam   
32           27                       1.0                     sam   
33           28                       1.0                     sam   
34           29                       1.0                     sam   
35           30                       1.0                     sam   
36           31                       1.0                     sam   
37           32                       1.0                     sam   
38           33                       1.0                     sam   
39           34                       1.0                     sam   
40           35                       1.0                     sam   
41           36                       1.0                     sam   
42           37                       1.0                     sam   
43           38                       1.0                     sam   
44           39                       1.0                     sam   
45           40                       1.0                     sam   
46           41                       1.0                     sam   
47           42                       1.0                     sam   
48           43                       NaN                    None   
49           44                       NaN                    None   
50           45                       NaN                    None   
51           46                       NaN                    None   
52           47                       NaN                    None   
53           48                       NaN                    None   
54           49                       NaN                    None   
55           50                       NaN                    None   
56           51                       1.0                     sam   
57  

In [40]:
##consider processing with order
query = '''
   SELECT
        s.sample_id,
        spstep.params AS params,
        MAX(CASE WHEN spstep.treatment_type = 'sam' THEN 1 ELSE 0 END) AS treatment_type_sam,
        MAX(CASE WHEN spstep.treatment_type = 'plasma_treatment' THEN 1 ELSE 0 END) AS treatment_type_plasma,
        MAX(CASE WHEN spstep.treatment_type = 'uv_ozone' THEN 1 ELSE 0 END) AS treatment_type_uv_ozone,
        
        CASE WHEN spstep.params ->> 'iupac_name' = 'water' THEN 1 ELSE 0 END AS is_water_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'isopropanol' THEN 1 ELSE 0 END AS is_isopropanol_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'ethanol' THEN 1 ELSE 0 END AS is_ethanol_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'acetone' THEN 1 ELSE 0 END AS is_acetone_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'methanol' THEN 1 ELSE 0 END AS is_methanol_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'piranha solution' THEN 1 ELSE 0 END AS is_piranha_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'PEIE' THEN 1 ELSE 0 END AS is_PEIE_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'RCA' THEN 1 ELSE 0 END AS is_RCA_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'toluene' THEN 1 ELSE 0 END AS is_toluene_treatment,
        
        
        MAX(CASE WHEN ststep.treatment_type = 'poor_solvent' THEN 1 ELSE 0 END) AS solution_treatment_poor_solvent,
        MAX(CASE WHEN ststep.treatment_type = 'aging' THEN 1 ELSE 0 END) AS solution_treatment_aging,
        MAX(CASE WHEN ststep.treatment_type = 'sonication' THEN 1 ELSE 0 END) AS solution_treatment_sonication,
        MAX(CASE WHEN ststep.treatment_type = 'mixing' THEN 1 ELSE 0 END) AS solution_treatment_mixing,
        MAX(CASE WHEN ststep.treatment_type = 'uv_irradiation' THEN 1 ELSE 0 END) AS solution_treatment_uv_irradiation,
    
    
        MAX(CASE WHEN ppstep.treatment_type = 'annealing' THEN 1 ELSE 0 END) AS post_process_annealing,
        MAX(CASE WHEN ppstep.treatment_type = 'drying' THEN 1 ELSE 0 END) AS  post_process_drying,
        MAX(CASE WHEN ppstep.treatment_type = 'chemical_treat' THEN 1 ELSE 0 END) AS post_process_chemical
        
       
    -- Add more similar lines for other treatment types as needed
    
    
     FROM
        SAMPLE s
    JOIN
        OFET_PROCESS of ON s.process_id = of.process_id
    LEFT JOIN 
        SUBSTRATE_PRETREAT_ORDER spo ON of.substrate_pretreat_id = spo.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_STEP spstep ON spstep.substrate_pretreat_step_id = spo.substrate_pretreat_step_id
    LEFT JOIN
        SOLUTION_TREATMENT_ORDER sto ON of.solution_treatment_id = sto.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_STEP ststep ON sto.solution_treatment_step_id = ststep.solution_treatment_step_id
    LEFT JOIN
        POSTPROCESS_ORDER ppo ON of.postprocess_id = ppo.postprocess_id
    LEFT JOIN
        POSTPROCESS_STEP ppstep ON ppo.postprocess_step_id = ppstep.postprocess_step_id
    GROUP BY
        s.sample_id,
        spstep.params
    ORDER BY
        s.sample_id ASC;

'''


# Use the read_select_query function to execute the query
result_df_chem1= read_select_query(query)

result_df_chem1  

#keep substrate_treatment_type_sam, aging, sonication,uv_irrad,pp_annealing. remove everything else

C:\Users\jbonsu3\AppData\Local\Temp\ipykernel_20988\1089282080.py:37: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query, conn)


sample_id                                             params  \
0             1                                               None   
1             2  {'sam_name': 'MTS', 'iupac_name': 'methyltrich...   
2             3  {'sam_name': 'PTS', 'iupac_name': 'phenyltrich...   
3             4  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
4             5  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
5             6  {'sam_name': 'MTS', 'iupac_name': 'methyltrich...   
6             6  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
7             7  {'sam_name': 'MTS', 'iupac_name': 'methyltrich...   
8             7  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
9             8  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
10            8  {'sam_name': 'PTS', 'iupac_name': 'phenyltrich...   
11            9  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
12            9  {'sam_name': 'PTS', 'iupac_name': 'phenyltrich...   
13           10  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
14           10  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
15           11  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
16           11  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
17           12                                               None   
18           13                                               None   
19           14                                               None   
20           15                                               None   
21           16                                               None   
22           17                                               None   
23           18                                               None   
24           19                                               None   
25           20                                               None   
26           21                                               None   
27           22                                               None   
28           23                                               None   
29           24  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
30           25  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
31           26  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
32           27  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
33           28  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
34           29  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
35           30  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
36           31  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
37           32  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
38           33  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
39           34  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
40           35  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
41           36  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
42           37  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
43           38  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
44           39  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
45           40  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
46           41  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
47           42  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
48           43                                               None   
49           44                                               None   
50           45                                               None   
51           46                                               None   
52           47                                               None   
53           48                                               None   
54           49                                               None   
55           50                                               None   
56           51 